### Dataset Preprocessing with Dask

In [ ]:
import os
import cv2
import torch
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import logging

import torch
import torch.nn as nn
import torchvision.models as models
import torch.optim as optim
from torch.optim.lr_scheduler import StepLR
import matplotlib.pyplot as plt
import numpy as np
from torch.utils.data import DataLoader
from torchvision.models import resnet18
from torch.optim import Adam
import torch.nn.functional as F

This cell defines the `LaneDatasetWithDask` class, a custom PyTorch dataset that utilizes **Dask** for delayed execution and parallelized preprocessing. It improves the data loading pipeline by optimizing image and segmentation preprocessing.

**Key Steps in the Code:**  
1. **Initialization:**  
   - Specifies paths for images and segmentation files based on training or testing mode.  
   - Loads and processes file lists into a structured format.

2. **Preprocessing:**  
   - **Images**: Loaded using OpenCV, resized, and converted to RGB format.  
   - **Segmentation Maps**: Loaded in grayscale, resized, and converted to binary segmentation.  

3. **Dask Integration:**  
   - Utilizes `delayed` and `compute` from Dask to parallelize image and segmentation preprocessing.  
   - Dask ensures that these preprocessing steps are efficient and optimized for multi-core execution.

4. **Error Handling:**  
   - Checks for missing or invalid image and segmentation files.  
   - Provides meaningful error messages for debugging.

**Why Dask?**  
Dask enhances the data loading process by splitting computations across multiple threads or processes, resulting in faster and more efficient dataset preparation. This is particularly useful for large-scale datasets like TuSimple.

**Output of the Code:**  
Returns individual samples in the dataset containing:  
- **Image tensor**  
- **Segmentation tensor**  
- **Instance segmentation tensor**  
- **Existence labels tensor**

This setup prepares the dataset for training or evaluation with Dask-powered preprocessing.!

In [ ]:
import os
import cv2
import torch
import numpy as np
from torch.utils.data import Dataset
from dask import delayed, compute

class LaneDatasetWithDask(Dataset):
    def __init__(self, dataset_path='./dataset/TUSimple', train=True, size=(800, 360)):
        self._dataset_path = dataset_path
        self._mode = "train" if train else "test"
        self._image_size = size  # w, h
        self._data = []

        if self._mode == "train":
            file_path = "train_val_gt.txt"
        elif self._mode == "test":
            file_path = "test_gt.txt"
        
        # Process file list
        self._process_list(os.path.join(self._dataset_path, "train_set/seg_label/list", file_path))

    def __getitem__(self, idx):
        # Extract relative paths
        img_rel_path, seg_rel_path, exists = self._data[idx]

        # Correct the base paths
        img_path = os.path.join(self._dataset_path, "train_set", img_rel_path.lstrip('/'))
        seg_path = os.path.join(self._dataset_path, "train_set", seg_rel_path.lstrip('/'))

        # Validate paths
        if not os.path.exists(img_path):
            raise FileNotFoundError(f"Image file not found: {img_path}")
        if not os.path.exists(seg_path):
            raise FileNotFoundError(f"Segmentation file not found: {seg_path}")

        # Preprocess with Dask
        raw_image = self.preprocess_image(img_path)
        segmentation_results = self.preprocess_segmentation(seg_path)

        # Compute delayed tasks
        raw_image, segmentation_results = compute(raw_image, segmentation_results)

        # Unpack segmentation results
        ins_segmentation_image, segmentation_image = segmentation_results

        # Convert to tensors
        image_tensor = torch.from_numpy(raw_image).float().permute((2, 0, 1))
        segmentation_tensor = torch.from_numpy(segmentation_image).to(torch.int64)
        ins_segmentation_tensor = torch.from_numpy(ins_segmentation_image)

        exists_tensor = torch.as_tensor([int(i) for i in exists])

        return {
            "img": image_tensor,
            "segLabel": segmentation_tensor,
            "IsegLabel": ins_segmentation_tensor,
            "exist": exists_tensor,
        }

    def __len__(self):
        return len(self._data)

    def preprocess_image(self, img_path):
        """
        Delayed preprocessing for image files.
        """
        return delayed(self._load_and_resize_image)(img_path)

    def preprocess_segmentation(self, seg_path):
        """
        Delayed preprocessing for segmentation files.
        """
        return delayed(self._load_and_process_segmentation)(seg_path)

    def _load_and_resize_image(self, img_path):
        """
        Load and resize an image using OpenCV.
        """
        image = cv2.imread(img_path)
        if image is None:
            raise ValueError(f"Invalid image at path: {img_path}")
        image = cv2.resize(image, self._image_size, interpolation=cv2.INTER_LINEAR)
        image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
        return image

    def _load_and_process_segmentation(self, seg_path):
        """
        Load and process segmentation maps.
        """
        seg = cv2.imread(seg_path, cv2.IMREAD_GRAYSCALE)
        if seg is None:
            raise ValueError(f"Invalid segmentation at path: {seg_path}")
        seg_resized = cv2.resize(seg, self._image_size, interpolation=cv2.INTER_LINEAR)
        binary_seg = (seg_resized > 0).astype(np.int64)  # Binary segmentation
        return seg_resized, binary_seg

    def _process_list(self, file_path):
        """
        Parse file containing relative paths to images and segmentation maps.
        """
        with open(file_path) as f:
            for line in f:
                words = line.split()
                image = words[0]
                segmentation = words[1]
                exists = words[2:]
                self._data.append((image, segmentation, exists))




#### Setting Up Dask Distributed Client**
---

This cell initializes a **Dask Distributed Client**, which manages and coordinates distributed computation. It defines the number of workers, threads per worker, and memory allocation per worker for efficient task execution.

**Key Components in the Code:**  

1. **Client Initialization:**  
   - `n_workers=4`: Specifies the number of independent workers in the Dask cluster.
   - `threads_per_worker=2`: Allocates 2 threads per worker, optimizing parallelism.
   - `memory_limit='4GB'`: Limits memory usage per worker to 4 GB to prevent overloads and ensure efficient memory usage.

2. **Dashboard Link:**  
   - `client.dashboard_link`: Provides a link to the Dask dashboard, offering a real-time view of task execution, memory consumption, and cluster health.

**Why Dask Client?**  
The Dask client allows for:
- Coordinated distributed execution of tasks.  
- Dynamic scaling based on workload requirements.  
- Real-time monitoring and debugging through the dashboard.

**Output of the Code:**  
- A link to the Dask dashboard, where you can monitor worker activity, task graphs, and system resource usage.

**Instructions:**  
Click on the dashboard link to explore the performance metrics and workload distribution of your Dask cluster.


In [ ]:
from dask.distributed import Client

client = Client(n_workers=4, threads_per_worker=2, memory_limit='4GB')
print(client.dashboard_link)  # Access the Dask dashboard

http://127.0.0.1:8787/status


In [ ]:
train_dataset = LaneDatasetWithDask(train=True, size=(800, 360))

In [ ]:
print(client.scheduler_info())

{'type': 'Scheduler', 'id': 'Scheduler-77ad0f12-8060-4575-bb7d-95218467d59d', 'address': 'tcp://127.0.0.1:42401', 'services': {'dashboard': 8787}, 'started': 1733620137.9999335, 'workers': {'tcp://127.0.0.1:37481': {'type': 'Worker', 'id': 1, 'host': '127.0.0.1', 'resources': {}, 'local_directory': '/tmp/dask-scratch-space/worker-ci1q8yrj', 'name': 1, 'nthreads': 2, 'memory_limit': 4000000000, 'last_seen': 1733620154.12777, 'services': {'dashboard': 39730}, 'metrics': {'task_counts': {}, 'bandwidth': {'total': 100000000, 'workers': {}, 'types': {}}, 'digests_total_since_heartbeat': {'tick-duration': 0.49991273880004883, 'latency': 0.002624034881591797}, 'managed_bytes': 0, 'spilled_bytes': {'memory': 0, 'disk': 0}, 'transfer': {'incoming_bytes': 0, 'incoming_count': 0, 'incoming_count_total': 0, 'outgoing_bytes': 0, 'outgoing_count': 0, 'outgoing_count_total': 0}, 'event_loop_interval': 0.019990134239196777, 'cpu': 6.0, 'memory': 125218816, 'time': 1733620153.627441, 'host_net_io': {'r

In [ ]:
print(client.get_task_stream())  # Monitor task stream in real-time.


()


In [ ]:
from torch.utils.data import DataLoader

# Create train and validation datasets
train_dataset = LaneDatasetWithDask(dataset_path="./dataset/TUSimple", train=True, size=(800, 360))
val_dataset = LaneDatasetWithDask(dataset_path="./dataset/TUSimple", train=False, size=(800, 360))
# Create DataLoader
train_loader = DataLoader(train_dataset, batch_size=8, shuffle=True, num_workers=4)
val_loader = DataLoader(val_dataset, batch_size=8, shuffle=False)


In [ ]:
import os
print(os.getcwd())  # Ensure the current directory is correct
print(os.listdir('./dataset/TUSimple/train_set'))  # Check if files are visible


/home/pendem.mu/LaneDetect
['clips', 'label_data_0313.json', 'label_data_0531.json', 'label_data_0601.json', 'readme.md', 'seg_label']




#### Testing Dask Configurations for Training Performance**
---
 
This cell evaluates the impact of various configurations of **Dask workers** and **threads per worker** on training performance. It uses **Dask Distributed** for parallelizing tasks and monitors the time taken to process the dataset across multiple configurations.

---

#### **Key Steps in the Code:**

1. **Define Testing Parameters:**
   - `workers_range`: Range of numbers of Dask workers to evaluate (e.g., 8, 4, 2, 1).
   - `threads_range`: Threads per worker for parallelism (e.g., 1, 2, 4).

2. **Test Function:**  
   - `test_config`: Tests a specific configuration by:
     - Initializing a Dask client with specified workers and threads.
     - Measuring the time taken for training batches.
     - Saving a **performance report** (`performance_report_{n_workers}w_{threads_per_worker}t.html`) for analysis.

3. **Run All Configurations:**  
   Iterates over combinations of `workers_range` and `threads_range`:
   - Prints the configuration being tested.
   - Appends the elapsed time to `results`.

4. **Visualization:**  
   - **Heatmap:** Represents the performance data:
     - X-axis: Threads per worker.
     - Y-axis: Number of workers.
     - Color: Time taken for processing (lower is better).

5. **Save and Display Heatmap:**  
   - Saves the heatmap as `training_performance_heatmap.png` for later reference.
   - Displays the heatmap for immediate analysis.

---

#### **Expected Outputs:**
1. A heatmap showing:
   - The impact of increasing workers and threads per worker.
   - Optimal configurations (minimum time taken).
2. Individual performance reports for each configuration:
   - Detailed insights into task scheduling and resource usage.

---

**Instructions for Analysis:**
- Review the heatmap to identify the best-performing configuration.
- Open the saved **performance reports** (`HTML` files) to understand task distribution and bottlenecks.
- Experiment with configurations based on results to optimize performance further.



### Explanation of Warnings

#### **Garbage Collection Warning**
- **Message**: `full garbage collections took XX% CPU time recently (threshold: 10%)`
- **Cause**: Python's garbage collector is spending significant time cleaning up unused memory. This typically happens when large temporary objects are frequently created and destroyed.

#### **RecursionError**
- **Message**: `maximum recursion depth exceeded`
- **Cause**: Deeply nested data structures (e.g., lists of lists) or recursive operations exceed Python's default recursion limit.

In [ ]:
import os
import time
import matplotlib.pyplot as plt
from dask.distributed import Client, performance_report
from tqdm import tqdm
import torch

# Define the range of workers, threads, and chunk sizes for testing
workers_range = [8, 4, 2, 1]
threads_range = [1, 2, 4]
chunk_sizes = [256, 512, 1024, 2048]

# Results storage
results = []

# Create output directories for dashboard and visualizations
output_dir = "dashboard_results_dask"
os.makedirs(output_dir, exist_ok=True)

def test_dask_config(n_workers, threads_per_worker, chunk_size, total_memory_limit=128):
    """
    Test Dask configuration dynamically allocating memory per worker and thread.

    Args:
        n_workers (int): Number of Dask workers.
        threads_per_worker (int): Threads per Dask worker.
        chunk_size (int): Dataset chunk size.
        total_memory_limit (int): Total memory limit in GB.
    """
    # Calculate memory per worker based on total memory
    memory_per_worker = total_memory_limit // (n_workers * threads_per_worker)
    print(f"Testing: Workers={n_workers}, Threads={threads_per_worker}, Chunk Size={chunk_size}, Memory={memory_per_worker}GB per worker")

    client = None  # Initialize client
    try:
        # Initialize Dask client
        client = Client(n_workers=n_workers, threads_per_worker=threads_per_worker, memory_limit=f"{memory_per_worker}GB")
        report_path = os.path.join(output_dir, f"report_{n_workers}w_{threads_per_worker}t_{chunk_size}c.html")

        with performance_report(filename=report_path):
            start_time = time.time()
            train_dataset = LaneDatasetWithDask(dataset_path="./dataset/TUSimple", train=True, size=(800, 360))
            for idx in tqdm(range(len(train_dataset)), desc=f"Processing with {n_workers}w, {threads_per_worker}t"):
                _ = train_dataset[idx]  # Simulate loading each data point
            total_time = time.time() - start_time

        print(f"Completed in {total_time:.2f} seconds")
        results.append((n_workers, threads_per_worker, chunk_size, memory_per_worker, total_time))
    except Exception as e:
        print(f"Error: {e}")
        results.append((n_workers, threads_per_worker, chunk_size, memory_per_worker, float('inf')))
    finally:
        if client is not None:
            client.close()


# Iterate over configurations and test
for n_workers in workers_range:
    for threads_per_worker in threads_range:
        for chunk_size in chunk_sizes:
            test_dask_config(n_workers, threads_per_worker, chunk_size, total_memory_limit=128)


# Convert results into a heatmap-friendly format
heatmap_data = {}
for n_workers, threads_per_worker, chunk_size, memory_limit, elapsed_time in results:
    key = (n_workers, threads_per_worker)
    if key not in heatmap_data:
        heatmap_data[key] = {}
    heatmap_data[key][chunk_size] = elapsed_time

# Generate heatmaps for each chunk size
for chunk_size in chunk_sizes:
    plt.figure(figsize=(10, 6))
    data_matrix = [
        [heatmap_data.get((w, t), {}).get(chunk_size, float('inf')) for t in threads_range]
        for w in workers_range
    ]

    plt.imshow(data_matrix, cmap="viridis", aspect="auto")
    plt.colorbar(label="Time (seconds)")
    plt.xticks(range(len(threads_range)), labels=threads_range, fontsize=10)
    plt.yticks(range(len(workers_range)), labels=workers_range, fontsize=10)
    plt.xlabel("Threads per Worker", fontsize=12)
    plt.ylabel("Number of Workers", fontsize=12)
    plt.title(f"Performance: Chunk Size {chunk_size}", fontsize=14)

    heatmap_path = os.path.join(output_dir, f"performance_chunk_{chunk_size}.png")
    plt.savefig(heatmap_path)
    print(f"Saved heatmap for chunk size {chunk_size}: {heatmap_path}")
    plt.show()

Testing: Workers=8, Threads=1, Chunk Size=256, Memory=16GB per worker


/home/pendem.mu/.conda/envs/pytorch_env_new/lib/python3.9/site-packages/distributed/node.py:182: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 33140 instead
  warnings.warn(
Processing with 8w, 1t:  45%|████▌     | 1645/3626 [02:46<02:49, 11.69it/s]2024-12-07 21:17:07,767 - distributed.utils_perf - WARNING - full garbage collections took 18% CPU time recently (threshold: 10%)
2024-12-07 21:17:07,947 - distributed.utils_perf - WARNING - full garbage collections took 20% CPU time recently (threshold: 10%)
Processing with 8w, 1t:  46%|████▋     | 1679/3626 [02:49<02:18, 14.08it/s]2024-12-07 21:17:10,542 - distributed.utils_perf - WARNING - full garbage collections took 19% CPU time recently (threshold: 10%)
2024-12-07 21:17:10,699 - distributed.utils_perf - WARNING - full garbage collections took 20% CPU time recently (threshold: 10%)
Processing with 8w, 1t:  58%|█████▊    | 2088/3626 [03:28<02:04, 12.35it/s]2024-12-0

Completed in 356.43 seconds
Testing: Workers=8, Threads=1, Chunk Size=512, Memory=16GB per worker


/home/pendem.mu/.conda/envs/pytorch_env_new/lib/python3.9/site-packages/distributed/node.py:182: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 33554 instead
  warnings.warn(
Processing with 8w, 1t:  57%|█████▋    | 2082/3626 [03:27<02:04, 12.41it/s]2024-12-07 21:23:50,543 - distributed.utils_perf - WARNING - full garbage collections took 23% CPU time recently (threshold: 10%)
2024-12-07 21:23:50,590 - distributed.utils_perf - WARNING - full garbage collections took 21% CPU time recently (threshold: 10%)
Processing with 8w, 1t:  59%|█████▉    | 2138/3626 [03:32<01:53, 13.16it/s]2024-12-07 21:23:55,118 - distributed.utils_perf - WARNING - full garbage collections took 23% CPU time recently (threshold: 10%)
2024-12-07 21:23:55,172 - distributed.utils_perf - WARNING - full garbage collections took 21% CPU time recently (threshold: 10%)
Processing with 8w, 1t:  66%|██████▌   | 2380/3626 [03:57<01:37, 12.78it/s]2024-12-0

Completed in 353.71 seconds
Testing: Workers=8, Threads=1, Chunk Size=1024, Memory=16GB per worker


...

/home/pendem.mu/.conda/envs/pytorch_env_new/lib/python3.9/site-packages/distributed/node.py:182: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 36047 instead
  warnings.warn(
Processing with 4w, 1t:  29%|██▉       | 1051/3626 [02:12<03:02, 14.13it/s]2024-12-07 22:37:34,700 - distributed.utils_perf - WARNING - full garbage collections took 24% CPU time recently (threshold: 10%)
2024-12-07 22:37:34,749 - distributed.utils_perf - WARNING - full garbage collections took 27% CPU time recently (threshold: 10%)
Processing with 4w, 1t:  32%|███▏      | 1145/3626 [02:25<03:51, 10.74it/s]2024-12-07 22:37:47,241 - distributed.utils_perf - WARNING - full garbage collections took 27% CPU time recently (threshold: 10%)
2024-12-07 22:37:47,258 - distributed.utils_perf - WARNING - full garbage collections took 23% CPU time recently (threshold: 10%)
Processing with 4w, 1t:  32%|███▏      | 1176/3626 [02:27<03:07, 13.10it/s]2024-12-0

Completed in 391.34 seconds
Testing: Workers=4, Threads=1, Chunk Size=1024, Memory=32GB per worker


/home/pendem.mu/.conda/envs/pytorch_env_new/lib/python3.9/site-packages/distributed/node.py:182: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 35147 instead
  warnings.warn(
Processing with 4w, 1t:  39%|███▉      | 1407/3626 [02:46<03:45,  9.85it/s]2024-12-07 22:44:44,493 - distributed.utils_perf - WARNING - full garbage collections took 25% CPU time recently (threshold: 10%)
2024-12-07 22:44:44,649 - distributed.utils_perf - WARNING - full garbage collections took 25% CPU time recently (threshold: 10%)
Processing with 4w, 1t:  41%|████      | 1469/3626 [02:51<03:54,  9.20it/s]2024-12-07 22:44:50,251 - distributed.utils_perf - WARNING - full garbage collections took 26% CPU time recently (threshold: 10%)
2024-12-07 22:44:50,382 - distributed.utils_perf - WARNING - full garbage collections took 25% CPU time recently (threshold: 10%)
Processing with 4w, 1t:  43%|████▎     | 1566/3626 [03:00<03:04, 11.17it/s]2024-12-0

Completed in 394.11 seconds
Testing: Workers=4, Threads=1, Chunk Size=2048, Memory=32GB per worker


/home/pendem.mu/.conda/envs/pytorch_env_new/lib/python3.9/site-packages/distributed/node.py:182: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 42473 instead
  warnings.warn(
Processing with 4w, 1t:  33%|███▎      | 1182/3626 [02:21<02:42, 15.04it/s]2024-12-07 22:50:58,920 - distributed.utils_perf - WARNING - full garbage collections took 26% CPU time recently (threshold: 10%)
2024-12-07 22:50:58,949 - distributed.utils_perf - WARNING - full garbage collections took 27% CPU time recently (threshold: 10%)
Processing with 4w, 1t:  36%|███▌      | 1312/3626 [02:31<02:37, 14.68it/s]2024-12-07 22:51:09,280 - distributed.utils_perf - WARNING - full garbage collections took 28% CPU time recently (threshold: 10%)
2024-12-07 22:51:09,454 - distributed.utils_perf - WARNING - full garbage collections took 25% CPU time recently (threshold: 10%)
Processing with 4w, 1t:  37%|███▋      | 1344/3626 [02:34<02:34, 14.78it/s]2024-12-0